In [ ]:
import cartopy.crs as ccrs
# import cartopy.feature as cf
import matplotlib.pyplot as plt
# import numpy as np

# import matplotlib.pyplot as plt
# from matplotlib import cm
import numpy as np
import h5py as h5py
# import cartopy.crs as ccrs
import cartopy.feature as cfeature
from cartopy.io.shapereader import Reader
from cartopy.feature import ShapelyFeature

%matplotlib notebook

projection = ccrs.PlateCarree()

fig = plt.figure(dpi=150)

ax = plt.axes(projection = projection)

ax.coastlines('10m')
ax.gridlines()
# ax.add_feature(cf.BORDERS)
# ax.add_feature(cf.STATES.with_scale('10m'))

# The extent bounds are specified as an array [[x0, y0], [x1, y1]], 
# where x0 is the left side of the extent, y0 is the top, x1 is the right and y1 is the bottom.
# extent (x0, x1, y0, y1)
# extent = [-180,180, -90,90] # world
# extent = [-90, -30, 20, -60] # south america
# extent = [-74, -31, 5.5, -33] # brazil
# extent = [-53.5, -45, -11, -20] # brazil
# extent = [-48, -47, -16, -17] # brazil
extent = [-44.996, -44.009, -2.805, -1.809] # brazil
# extent = [-90, -30, 20, -60]
# extent = [-100, 30, 0, 80]
# extent = [-87.35, -79.5, 24.1, 30.8]


ax.set_extent(extent, crs=ccrs.PlateCarree())



In [ ]:
# First: read the geotiff image with GDAL.
from osgeo import gdal, osr

gdal.UseExceptions()

fname = '/notebooks/resources/T23MNT_20190525T132241_TCI_60m.jp2'

ds = gdal.Open(fname)
data = ds.ReadAsArray()
gt = ds.GetGeoTransform()
proj = ds.GetProjection()

inproj = osr.SpatialReference()
inproj.ImportFromWkt(proj)

print('\n\n## ds ##:\n\n' + str(ds))
print('\n\n## data ##:\n\n' + str(data))
print('\n\n## gt ##:\n\n' + str(gt))
print('\n\n## proj ##:\n\n' + str(proj))
print('\n\n## inproj ##:\n\n' + str(inproj))

In [ ]:
projcs = inproj.GetAuthorityCode('PROJCS')
print('\n\n## projcs ##:\n\n' + str(projcs))

image_projection = ccrs.epsg(projcs)
print('\n\n## image_projection ##:\n\n' + str(image_projection))

In [ ]:
img = plt.imread(fname)

In [ ]:
# import cartopy.crs as ccrs
# import cartopy.feature as cf
# import matplotlib.pyplot as plt
# %matplotlib inline

projection = ccrs.PlateCarree()

fig = plt.figure(dpi=100)

ax = plt.axes(projection = projection)

ax.coastlines('10m')
ax.gridlines()

# The extent bounds are specified as an array [[x0, y0], [x1, y1]], 
# where x0 is the left side of the extent, y0 is the top, x1 is the right and y1 is the bottom.
extent = [-44.996, -44.009, -2.805, -1.809] # são luíz do maranhão

ax.set_extent(extent, crs=ccrs.PlateCarree())
img = plt.imread(fname)
ax.imshow(img, extent=extent, origin='upper', transform=ccrs.PlateCarree())

# plt.show()

print('\n\n## get_extent() ##:\n\n' + str(ax.get_extent()))

In [ ]:
# import matplotlib.pyplot as plt
# from matplotlib import cm
# import numpy as np
# import h5py as h5py
# import cartopy.crs as ccrs
# import cartopy.feature as cfeature
# from cartopy.io.shapereader import Reader
# from cartopy.feature import ShapelyFeature
# %matplotlib inline

hdf5 = '/notebooks/resources/3B-MO.MS.MRG.3IMERG.20190101-S000000-E235959.01.V06A.HDF5'
dataset = h5py.File(hdf5,'r')

precip = dataset['Grid/precipitation'][:]
precip = np.transpose(precip[0])

theLats = dataset['Grid/lat'][:]
theLons = dataset['Grid/lon'][:]

# [-44.996, -44.009, -2.805, -1.809]

condition = ((theLats < -44) & (theLats > -45))
extractedLats = np.extract(condition, theLats)

# print(theLats[(theLats < -44) & (theLats > -45)])
# print(theLats[condition])
# print(extractedLats)

condition = ((theLons < -1.809) & (theLons > -2.805))
extractedLons = np.extract(condition, theLons)

# print(theLons[(theLons < -1.809) & (theLons > -2.805)])
# print(theLons[condition])
# print(extractedLons)

clevs = np.arange(0,1.26,0.125)

x, y = np.float32(np.meshgrid(theLons, theLats))
# x, y = np.float32(np.meshgrid(extractedLons, extractedLats))

masked_array = np.ma.masked_where(precip < 0,precip)

cmap = 'nipy_spectral'

plt.title('January 2019 Monthly Average Rain Rate')

font = {'weight' : 'bold', 'size' : 3}

plt.rc('font', **font)

plt.xlim(-2.805, -1.809)
plt.ylim(-45, -44)

# cs = ax.contourf(np.reshape(x, precip), np.reshape(y, precip), precip, clevs, transform=ccrs.PlateCarree(), cmap=cmap)
cs = ax.contourf(x, y, precip, clevs, transform=ccrs.PlateCarree(), cmap=cmap)

sm = plt.cm.ScalarMappable(cmap=cmap,norm=plt.Normalize(0,1))
sm._A = []
plt.colorbar(sm, ax=ax, label='mm/h', shrink=0.5)

# plt.show()